In [ ]:
!pip install gradio
!pip install langchain bitsandbytes
!pip install faiss-cpu
!pip install textwrap torch datasets loralib sentencepiece
!pip install sentence-transformers
!pip install accelerate
!pip install llama-cpp-python
!pip -q install git+https://github.com/huggingface/transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.7/19.7 MB 80.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.0/57.0 kB 7.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 288.4/288.4 kB 32.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.4/75.4 kB 10.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 31.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.5/50.5 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 137.0/137.0 kB 17.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.7/45.7 kB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.9/129.9 kB 17.7 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of mdit-py-plugins to determine which version is compatible with other requirements. This could take a while.
 

In [ ]:
# !cd llama.cpp && pwd

In [ ]:
# !git clone https://github.com/ggerganov/llama.cpp
# !cd llama.cpp && make

In [ ]:
# !ls ./models

In [ ]:
!gdown 1oSCsACt5FrBLCD_T5FTzremT5y2b2KxK
!gdown 1989gHL2kGm1sSLuVKk6ao8loGLvt8uR-
!mkdir nbdt_data
!cp index.faiss nbdt_data
!cp index.pkl nbdt_data

Downloading...
From: https://drive.google.com/uc?id=1oSCsACt5FrBLCD_T5FTzremT5y2b2KxK
To: /content/index.faiss
100% 121M/121M [00:04<00:00, 27.5MB/s]
Downloading...
From: https://drive.google.com/uc?id=1989gHL2kGm1sSLuVKk6ao8loGLvt8uR-
To: /content/index.pkl
100% 37.5M/37.5M [00:01<00:00, 29.2MB/s]


In [29]:
import gradio as gr
from langchain.vectorstores import FAISS
from langchain.embeddings import HuggingFaceEmbeddings
from transformers import LlamaTokenizer, LlamaForCausalLM, GenerationConfig, pipeline
from transformers import BitsAndBytesConfig
import textwrap
import torch

quant_config = BitsAndBytesConfig(load_in_4bit=True,
                                         bnb_4bit_compute_dtype=torch.bfloat16,
                                         bnb_4bit_use_double_quant=True,
                                         )

prompt = 'BEGINNING OF CONVERSATION: USER: \
I will provide you with two abstracts, I intend to use the author of the second to review the first. Tell me in 15 words why or why not the second author is a good fit to review the first paper.\n\
Abstract To Be Reviewed: '

tokenizer = LlamaTokenizer.from_pretrained("samwit/koala-7b")

base_model = LlamaForCausalLM.from_pretrained(
    "samwit/koala-7b",
    load_in_8bit=False,
    load_in_4bit=True,
    device_map='auto',
    offload_folder='offloaded',
    quantization_config=quant_config
)

pipe = pipeline(
    "text-generation",
    model=base_model,
    tokenizer=tokenizer,
    max_length=1024,
    temperature=0.7,
    top_p=0.95,
    repetition_penalty=1.15,
    # device=-1
)


def wrap_text_preserve_newlines(text, width=110):
    # Split the input text into lines based on newline characters
    lines = text.split('\n')
    # Wrap each line individually
    wrapped_lines = [textwrap.fill(line, width=width) for line in lines]
    # Join the wrapped lines back together using newline characters
    wrapped_text = '\n'.join(wrapped_lines)
    return wrapped_text


def create_miread_embed(sents, bundle):
    tokenizer = bundle[0]
    model = bundle[1]
    model.cpu()
    tokens = tokenizer(sents,
                       max_length=512,
                       padding=True,
                       truncation=True,
                       return_tensors="pt"
                       )
    device = torch.device('cpu')
    tokens = tokens.to(device)
    with torch.no_grad():
        out = model.bert(**tokens)
        feature = out.last_hidden_state[:, 0, :]
    return feature.cpu()


def get_matches(query, k):
    matches = vecdb.similarity_search_with_score(query, k=k)
    return matches


def inference(query,k=30,mode=''):
    matches = get_matches(query,k)
    j_bucket = {}
    n_table = []
    a_table = []
    r_table = []
    scores = [round(match[1].item(),3) for match in matches]
    min_score = min(scores)
    max_score = max(scores)
    normaliser = lambda x: round(1 - (x-min_score)/max_score,3)
    for i,match in enumerate(matches):
        doc = match[0]
        score = normaliser(round(match[1].item(),3))
        title = doc.metadata['title']
        author = doc.metadata['authors'][0]
        date = doc.metadata.get('date','None')
        link = doc.metadata.get('link','None')
        submitter = doc.metadata.get('submitter','None')
        journal = doc.metadata.get('journal','None')
        abstract = doc.metadata.get('abstract','')

        # For journals
        if journal not in j_bucket:
            j_bucket[journal] = score
        else:
            j_bucket[journal] += score

        # For authors
        record = [i+1,
                  score,
                  author,
                  title,
                  link,
                  date]
        n_table.append(record)

        # For abstracts
        record = [i+1,
                  title,
                  author,
                  submitter,
                  journal,
                  date,
                  link,
                  score
        ]
        a_table.append(record)

        # For reviewer
        r_record = [i+1,
                    score,
                    author,
                    abstract,
                    title,
                    link,
                    date]
        r_table.append(r_record)



    if (mode):
      dataset = [prompt + query + '\n Candidate Abstract: ' + row[3] + '\n GPT:' for row in r_table[:5]]
      outputs = pipe(dataset)
      outputs = [output[0]['generated_text'].split('GPT:')[1] for output in outputs]
      r_table = [[r[0],r[1],r[2],outputs[i],r[4],r[5],r[6]] for i,r in enumerate(r_table[:5])]
      # print(f"{i}/5 done")
    else:
      outputs = ['']*5
      r_table = [[r[0],r[1],r[2],outputs[i],r[4],r[5],r[6]] for i,r in enumerate(r_table[:5])]

    j_table = sorted([[journal,score] for journal,score in j_bucket.items()],key= lambda x : x[1],reverse=True)
    j_table = [[i+1,item[0],item[1]] for i,item in enumerate(j_table)]
    j_output= gr.Dataframe.update(value=j_table,visible=True)
    n_output= gr.Dataframe.update(value=n_table,visible=True)
    a_output = gr.Dataframe.update(value=a_table,visible=True)
    if mode:
      r_output = gr.Dataframe.update(value=r_table,visible=True)
      return r_output

    return [a_output,j_output,n_output]

def k_inference(query,k):
  return inference(query,k,'koala')

model_name = "biodatlab/MIReAD-Neuro-Large"
model_kwargs = {'device': 'cpu'}
encode_kwargs = {'normalize_embeddings': False}
faiss_embedder = HuggingFaceEmbeddings(
    model_name=model_name,
    model_kwargs=model_kwargs,
    encode_kwargs=encode_kwargs
)

vecdb = FAISS.load_local("nbdt_data", faiss_embedder)


with gr.Blocks(theme=gr.themes.Soft()) as demo:
    gr.Markdown("# NBDT Recommendation Engine for Editors")
    gr.Markdown("NBDT Recommendation Engine for Editors is a tool for neuroscience authors/abstracts/journalsrecommendation built for NBDT journal editors. \
    It aims to help an editor to find similar reviewers, abstracts, and journals to a given submitted abstract.\
    To find a recommendation, paste a `title[SEP]abstract` or `abstract` in the text box below and click \"Find Matches\".\
    Then, you can hover to authors/abstracts/journals tab to find a suggested list.\
    The data in our current demo is selected from 2018 to 2022. We will update the data monthly for an up-to-date publications.")


    abst = gr.Textbox(label="Abstract",lines=10)

    k = gr.Slider(1,100,step=1,value=50,label="Number of matches to consider")

    action_btn = gr.Button(value="Find Matches")

    with gr.Tab("Authors"):
        n_output = gr.Dataframe(
            headers=['No.','Score','Name','Title','Link','Date'],
            datatype=['number','number','str','str','str','str'],
            col_count=(6, "fixed"),
            wrap=True,
            visible=False
        )
    with gr.Tab("Abstracts"):
        a_output = gr.Dataframe(
            headers=['No.','Title','Author','Corresponding Author','Journal','Date','Link','Score'],
            datatype=['number','str','str','str','str','str','str','number'],
            col_count=(8,"fixed"),
            wrap=True,
            visible=False
        )
    with gr.Tab("Journals"):
        j_output = gr.Dataframe(
            headers=['No.','Name','Score'],
            datatype=['number','str','number'],
            col_count=(3, "fixed"),
            wrap=True,
            visible=False
        )

    llm_btn = gr.Button(value="Listen to Koala's advice")
    with gr.Tab("Reviewers (New)"):
      r_output = gr.Dataframe(
          headers=['No.','Score','Name','Title','Reasoning','Link','Date'],
          datatype=['number','number','str','str','str','str','str'],
          col_count=(7,"fixed"),
          wrap=True,
          visible=True
      )

    action_btn.click(fn=inference,
                     inputs=[
                            abst,
                            k,
                            # modes,
                            ],
                     outputs=[a_output,j_output,n_output],
                     api_name="neurojane")
    llm_btn.click(fn=k_inference,
                  inputs=[
                      abst,
                      k,
                  ],
                  outputs = [r_output],
                  api_name="koala")

demo.launch(debug=True,share=True)

Loading checkpoint shards:   0%|          | 0/14 [00:00<?, ?it/s]

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
Running on public URL: https://1ceb8c0439dfe6906c.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


Keyboard interruption in main thread... closing server.


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ /usr/local/lib/python3.10/dist-packages/gradio/blocks.py:2058 in block_thread                    │
│                                                                                                  │
│   2055 │   │   """Block main thread until interrupted by user."""                                │
│   2056 │   │   try:                                                                              │
│   2057 │   │   │   while True:                                                                   │
│ ❱ 2058 │   │   │   │   time.sleep(0.1)                                                           │
│   2059 │   │   except (KeyboardInterrupt, OSError):                                              │
│   2060 │   │   │   print("Keyboard interruption in main thread... closing server.")              │
│   2061 │   │   │   self.server.close()                                                           │
╰──────────────────────────────────────────────────────────────────────────────────────────────────╯
KeyboardInterrupt

During handling of the above exception, another exception occurred:

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <cell line: 236>:236                                                                          │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/gradio/blocks.py:1970 in launch                          │
│                                                                                                  │
│   1967 │   │                                                                                     │
│   1968 │   │   # Block main thread if debug==True                                                │
│   1969 │   │   if debug or int(os.getenv("GRADIO_DEBUG", 0)) == 1:                               │
│ ❱ 1970 │   │   │   self.block_thread()                                                           │
│   1971 │   │   # Block main thread if running in a script to stop script from exiting            │
│   1972 │   │   is_in_interactive_mode = bool(getattr(sys, "ps1", sys.flags.interactive))         │
│   1973                                                                                           │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/gradio/blocks.py:2061 in block_thread                    │
│                                                                                                  │
│   2058 │   │   │   │   time.sleep(0.1)                                                           │
│   2059 │   │   except (KeyboardInterrupt, OSError):                                              │
│   2060 │   │   │   print("Keyboard interruption in main thread... closing server.")              │
│ ❱ 2061 │   │   │   self.server.close()                                                           │
│   2062 │   │   │   for tunnel in CURRENT_TUNNELS:                                                │
│   2063 │   │   │   │   tunnel.kill()                                                             │
│   2064                                                                                           │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/gradio/networking.py:43 in close                         │
│                                                                                                  │
│    40 │                                                                                          │
│    41 │   def close(self):                                                                       │
│    42 │   │   self.should_exit = True                                   

In [30]:
k_inference('The experimental study of learning and plasticity has always been driven by an implicit question: how can physiological changes be adaptive and improve performance? For example, in Hebbian plasticity only synapses from presynaptic neurons that were active are changed, avoiding useless changes. Similarly, in dopamine-gated learning synapse changes depend on reward or lack thereof and do not change when everything is predictable. Within machine learning we can make the question of which changes are adaptive concrete: performance improves when changes correlate with the gradient of an objective function quantifying performance. This result is general for any system that improves through small changes. As such, physiology has always implicitly been seeking mechanisms that allow the brain to approximate gradients. Coming from this perspective we review the existing literature on plasticity-related mechanisms, and we show how these mechanisms relate to gradient estimation. We argue that gradients are a unifying idea to explain the many facets of neuronal plasticity.',k=10)

{'max_rows': None,
 'max_cols': None,
 'label': None,
 'show_label': None,
 'scale': None,
 'min_width': None,
 'interactive': None,
 'visible': True,
 'value': [[1,
   1.0,
   'philipp berens',
   " Both authors have expertise in neuroscience and machine learning, making them suitable candidates to review each other's work. The first author's research focuses on understanding the mechanisms underlying learning and plasticity, while the second author's work involves developing new algorithms for spike inference from calcium signals. These areas of expertise complement each other, as the first author's insights into the nature of plasticity can inform the development of more effective spike inference algorithms.",
   'Supervised learning sets benchmark for robust spike detection from calcium imaging signals',
   'https://www.semanticscholar.org/paper/786f9831900ca34d8200291e5a72d2f14ad9b336',
   2015],
  [2,
   0.974,
   'daniel butts',
   " Both authors have expertise in neuroscience a